In [ ]:
!pip install xarray
!pip install pandas
!pip install ecmwf-opendata
!pip install hvplot

In [17]:
import xarray as xr
import pandas as pd
from ecmwf.opendata import Client
import hvplot.xarray

In [18]:

client = Client("ecmwf", beta=False)
parameters = ['tp']
filename = 'medium-rain-acc.grib'
filename

'medium-rain-acc.grib'

In [19]:

client.retrieve(
    step=240,
    stream="oper",
    type="fc",
    levtype="sfc",
    resol='0p25',
    param=parameters,
    target=filename
)



In [20]:
euro = xr.open_dataset(filename, engine='cfgrib')

Ignoring index file 'medium-rain-acc.grib.5b7b6.idx' older than GRIB file
C:\Users\john.collop\PycharmProjects\pythonProject\.venv\New\Lib\site-packages\cfgrib\xarray_plugin.py:131: FutureWarning: In a future version of xarray decode_timedelta will default to False rather than None. To silence this warning, set decode_timedelta to True, False, or a 'CFTimedeltaCoder' instance.
  vars, attrs, coord_names = xr.conventions.decode_cf_variables(


In [21]:
df = pd.read_csv(r'acres.csv')

In [23]:
import geopandas as gpd
import geoviews as gv

counties = gpd.read_file(r'https://gist.githubusercontent.com/sdwfrost/d1c73f91dd9d175998ed166eb216994a/raw/e89c35f308cee7e2e5a784e1d3afc5d449e9e4bb/counties.geojson')

In [26]:
joint = counties.set_index('GEOID').join(df.set_index('ANSI')).dropna(subset=['VALUE'])

In [27]:
joint.sort_values('VALUE', ascending=False, inplace=True)
joint.rename(columns={'VALUE':'RAINFED_ACRES'}, inplace=True)

In [28]:
joint

STATEFP COUNTYFP  COUNTYNS        AFFGEOID      NAME LSAD        ALAND  \
GEOID                                                                          
48305      48      305  01383938  0500000US48305      Lynn   06   2309924845   
48115      48      115  01383843  0500000US48115    Dawson   06   2331781556   
48165      48      165  01383868  0500000US48165    Gaines   06   3891105276   
48219      48      219  01383895  0500000US48219   Hockley   06   2352723906   
48445      48      445  01384008  0500000US48445     Terry   06   2302083289   
...       ...      ...       ...             ...       ...  ...          ...   
01057      01      057  00161554  0500000US01057   Fayette   06   1625693280   
35013      35      013  00929109  0500000US35013  Doña Ana   06   9863129996   
13167      13      167  00346664  0500000US13167   Johnson   06    784793323   
40103      40      103  01101839  0500000US40103     Noble   06   1895593648   
06107      06      107  00277318  0500000US06107    Tulare   06  12494838453   

         AWATER                                           geometry  \
GEOID                                                                
48305   4169719  POLYGON ((-102.07593 33.38959, -101.55688 33.3...   
48115   4720730  POLYGON ((-102.20852 32.95896, -102.07621 32.9...   
48165   1262946  POLYGON ((-103.06489 32.84936, -103.06347 32.9...   
48219    446119  POLYGON ((-102.61545 33.82512, -102.08573 33.8...   
48445   5443861  POLYGON ((-102.59484 33.38849, -102.07593 33.3...   
...         ...                                                ...   
01057   4330881  POLYGON ((-87.95178 33.91993, -87.73935 33.914...   
35013  17627587  POLYGON ((-107.29948 32.78017, -106.88773 32.7...   
13167   9278537  POLYGON ((-82.94697 32.75936, -82.80246 32.809...   
40103  27552185  POLYGON ((-97.4616 36.59364, -97.05741 36.5936...   
06107  37259234  POLYGON ((-119.54613 36.50896, -119.46632 36.5...   

                                   LOCATION_DESC STATE_ANSI COUNTY_ANSI  \
GEOID                                                                     
48305          TEXAS, SOUTHERN HIGH PLAINS, LYNN         48         305   
48115        TEXAS, SOUTHERN HIGH PLAINS, DAWSON         48         115   
48165        TEXAS, SOUTHERN HIGH PLAINS, GAINES         48         165   
48219       TEXAS, SOUTHERN HIGH PLAINS, HOCKLEY         48         219   
48445         TEXAS, SOUTHERN HIGH PLAINS, TERRY         48         445   
...                                          ...        ...         ...   
01057  ALABAMA, UPPER PLAINS & PIEDMONT, FAYETTE         01         057   
35013            NEW MEXICO, SOUTHEAST, DONA ANA         35         013   
13167                  GEORGIA, CENTRAL, JOHNSON         13         167   
40103             OKLAHOMA, NORTH CENTRAL, NOBLE         40         103   
06107     CALIFORNIA, SAN JOAQUIN VALLEY, TULARE         06         107   

       RAINFED_ACRES  
GEOID                 
48305       341500.0  
48115       330500.0  
48165       292500.0  
48219       259000.0  
48445       254000.0  
...              ...  
01057         1700.0  
35013         1300.0  
13167         1300.0  
40103         1000.0  
06107          900.0  

[281 rows x 13 columns]

In [29]:
(euro['tp']*39.37).hvplot(height=600, width=1250, coastline=True, features={'states':'50m'}) * gv.Polygons(joint[['LOCATION_DESC','RAINFED_ACRES','geometry']]).opts(color='RAINFED_ACRES',alpha=0.25, cmap='kgy')

:Overlay
   .Image.I     :Image   [longitude,latitude]   (tp)
   .Coastline.I :Feature   [Longitude,Latitude]
   .States.I    :Feature   [Longitude,Latitude]
   .Polygons.I  :Polygons   [Longitude,Latitude]   (LOCATION_DESC,RAINFED_ACRES)